# Astrophysics III: galaxy formation & evolution
Moodle: https://go.epfl.ch/PHYS-465

## Exercise 11
Teaching assistant: Jonathan Petersson <br>
Email: jonathan.petersson@epfl.ch

***

In [ ]:
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
from mpl_toolkits.axes_grid1 import make_axes_locatable


%matplotlib notebook
plt.rcParams['font.size'] = 14

# Load data:
data_dm_winds = np.loadtxt('DMParticles_M3852_winds_z0.dat')
data_dm_nomw  = np.loadtxt('DMParticles_M3852_nomw_z0.dat')

data_star_winds = np.loadtxt('StarParticles_M3852_winds_z0.dat')
data_star_nomw  = np.loadtxt('StarParticles_M3852_nomw_z0.dat')

data_gas_winds = np.loadtxt('GasParticles_M3852_winds_z0.dat')
data_gas_nomw  = np.loadtxt('GasParticles_M3852_nomw_z0.dat')

## Exercise 11.1:

In [ ]:
# Stellar Baryon Conversion Efficiency:
Omega_b = 0.04087
Omega_m = 0.259 
fbar = Omega_b / Omega_m

Rvir = 109  # [kpc/h]
Rgal = 0.1 * Rvir

Mstellar_winds = np.sum(data_star_winds[:,0][np.linalg.norm(data_star_winds[:,1:], axis=1) < Rgal])
Mstellar_nomw =  np.sum(data_star_nomw[:,0][np.linalg.norm(data_star_nomw[:,1:], axis=1) < Rgal])

Mdm_winds = np.sum(data_dm_winds[:,0][np.linalg.norm(data_dm_winds[:,1:], axis=1) < Rvir])
Mdm_nomw = np.sum(data_dm_nomw[:,0][np.linalg.norm(data_dm_nomw[:,1:], axis=1) < Rvir])

sbce_winds = Mstellar_winds / (fbar * Mdm_winds)
sbce_nomw = Mstellar_nomw / (fbar * Mdm_nomw)

print('Momentum-driven winds stellar feedback')
print(f'Mhalo: {Mdm_winds}')
print(f'sbce: {sbce_winds}\n')

print('Thermal (weak) stellar feedback')
print(f'Mhalo: {Mdm_nomw}')
print(f'sbce: {sbce_nomw}')

## Exercise 11.2:

Kepler's third law states that:

\begin{equation}
    \frac{a^3}{T^2} = \frac{G(M + m)}{4 \pi^2}. 
\end{equation}

For a circular orbit where $a=r$, $T=(2\pi r)/v_\mathrm{circ}$ and $M >> m$, Kepler's law gives us that

\begin{equation}
    \frac{r^3}{\left(\frac{2\pi r}{v_\mathrm{circ}}\right)^2} = \frac{GM}{4\pi^2} \quad \Rightarrow \quad v_\mathrm{circ} = \sqrt{\frac{GM}{r}}. 
\end{equation}

## Exercise 11.3:

In [ ]:
G = 6.67430e-8   #[cgs]
Msol = 1.989e33  #[g]
kpc = 3.086e21   #[cm]

# Circular velocity:
radius = np.linspace(0, 20, 100)

vc_winds = {
    'dm'    : [],
    'star'  : [],
    'gas'   : [],
    'total' : []
}

vc_nomw = {
    'dm'    : [],
    'star'  : [],
    'gas'   : [],
    'total' : []
}

for i in range(1, len(radius)):
    mass_dm = np.sum(data_dm_winds[:,0][np.linalg.norm(data_dm_winds[:,1:], axis=1) < radius[i]])
    mass_star = np.sum(data_star_winds[:,0][np.linalg.norm(data_star_winds[:,1:], axis=1) < radius[i]])
    mass_gas = np.sum(data_gas_winds[:,0][np.linalg.norm(data_gas_winds[:,1:], axis=1) < radius[i]])
    mass_total = mass_dm + mass_star + mass_gas
    
    vc_winds['dm'].append(np.sqrt(G * mass_dm * 1e10* Msol / (radius[i] * kpc)) / 1e5)
    vc_winds['star'].append(np.sqrt(G * mass_star * 1e10 * Msol / (radius[i] * kpc)) / 1e5)
    vc_winds['gas'].append(np.sqrt(G * mass_gas * 1e10 * Msol / (radius[i] * kpc)) / 1e5)
    vc_winds['total'].append(np.sqrt(G * mass_total * 1e10 * Msol / (radius[i] * kpc)) / 1e5)
    
    mass_dm = np.sum(data_dm_nomw[:,0][np.linalg.norm(data_dm_nomw[:,1:], axis=1) < radius[i]])
    mass_star = np.sum(data_star_nomw[:,0][np.linalg.norm(data_star_nomw[:,1:], axis=1) < radius[i]])
    mass_gas = np.sum(data_gas_nomw[:,0][np.linalg.norm(data_gas_nomw[:,1:], axis=1) < radius[i]])
    mass_total = mass_dm + mass_star + mass_gas
    
    vc_nomw['dm'].append(np.sqrt(G * mass_dm * 1e10* Msol / (radius[i] * kpc)) / 1e5)
    vc_nomw['star'].append(np.sqrt(G * mass_star * 1e10 * Msol / (radius[i] * kpc)) / 1e5)
    vc_nomw['gas'].append(np.sqrt(G * mass_gas * 1e10 * Msol / (radius[i] * kpc)) / 1e5)
    vc_nomw['total'].append(np.sqrt(G * mass_total * 1e10 * Msol / (radius[i] * kpc)) / 1e5)

In [ ]:
fig, ax = plt.subplots(1, 2, figsize=(10, 4), sharey=True, layout='constrained')

ax[0].plot(radius[1:], vc_winds['dm'], lw=2, c='blue', alpha=0.5, label='DM')
ax[0].plot(radius[1:], vc_winds['star'], lw=2, c='red', alpha=0.5, label='Stars')
ax[0].plot(radius[1:], vc_winds['gas'], lw=2, c='orange', alpha=0.5, label='Gas')
ax[0].plot(radius[1:], vc_winds['total'], lw=2, c='k', alpha=0.5, label='Total')
ax[0].set_xlabel('Radius [kpc]')
ax[0].set_ylabel('$v_\mathrm{circ} \ [\mathrm{km \ s}^{-1}]$')
ax[0].set_title('winds')
ax[0].legend(frameon=False)

ax[1].plot(radius[1:], vc_nomw['dm'], lw=2, c='blue', alpha=0.5,)
ax[1].plot(radius[1:], vc_nomw['star'], lw=2, c='red', alpha=0.5)
ax[1].plot(radius[1:], vc_nomw['gas'], lw=2, c='orange', alpha=0.5)
ax[1].plot(radius[1:], vc_nomw['total'], lw=2, c='k', alpha=0.5)
ax[1].set_xlabel('Radius [kpc]')
ax[1].set_title('nomw')

fig.savefig('ex3.pdf')
plt.show()

## Exercise 11.4:

In [ ]:
fig, ax = plt.subplots(figsize=(8, 6), layout='constrained')

# Avila-Reese et al. (2008):
mstellar = np.logspace(9, 11, 100)
logvmax = 0.274 * np.log10(mstellar) - 0.639
err = 0.058
ax.fill_between(np.log10(mstellar), logvmax-err, logvmax+err, color='k', edgecolor='none', alpha=0.2)
ax.plot(np.log10(mstellar), logvmax, ls='--', lw=2, c='k', label='Avila-Reese+2008')

# Maximum circular velocity & stellar mass:
vmax_winds = np.max(vc_winds['total'])
mstellar_winds = np.sum(data_star_winds[:,0][np.linalg.norm(data_star_winds[:,1:], axis=1) < Rgal]) * 1e10
ax.scatter(np.log10(mstellar_winds), np.log10(vmax_winds), s=300, marker='*', c='blue', label='winds')

vmax_nomw = np.max(vc_nomw['total'])
mstellar_nomw = np.sum(data_star_nomw[:,0][np.linalg.norm(data_star_nomw[:,1:], axis=1) < Rgal]) * 1e10
ax.scatter(np.log10(mstellar_nomw), np.log10(vmax_nomw), s=300, marker='*', c='red', label='nomw')

ax.set_xlabel('$\log_{10}(M_\star \ [\mathrm{M}_\odot])$')
ax.set_ylabel('$\log_{10}(v_\mathrm{max} \ [\mathrm{km s}^{-1}])$')
ax.set_xlim(9, 11)
ax.legend(frameon=False)

fig.savefig('ex4.pdf')
plt.show()